In [2]:
import pandas as pd
import json
with open('/home/keshavsingh/keshav-nlp2019/data/practice.jsonl') as f:
    data = [json.loads(line) for line in f]

In [3]:
import os,random
from random import seed
from collections import defaultdict
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '2'
import csv, sys, nltk
import numpy as np
from numpy import zeros
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.text import text_to_word_sequence
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Concatenate,Activation,Embedding, Flatten, Dense, LSTM, Multiply, Input, Dot, Dropout, Bidirectional, Lambda, Subtract
from keras.models import Sequential, Model
from keras.callbacks import EarlyStopping, ModelCheckpoint
import keras
import tensorflow as tf
import itertools

Using TensorFlow backend.


In [4]:
total_p, total_c, total_w, labels = [], [], [], []
for sentence in data:
    total_p.append(sentence["premise"])
    total_c.append(sentence["claim"])
  #  total_w.append(sentence["warrant"])
    labels.append(sentence["label"])

In [5]:
total_c

['exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'exposure to violent video games causes at least a temporary increase

In [6]:
total_p

[['The most recent large scale meta-anlysis-- examining 130 studies with over 130,000 subjects worldwide-- concluded that exposure to violent video games causes both short term and long term aggression in players',
  'On November 29, 2010 in South Philadelphia, Pennsylvania, 16-year-old boy Kendall Anderson bludgeoned his mother to death in her sleep with a claw hammer after she took away his PlayStation [REF',
  'A meta-analysis by psychologist Jonathan Freedman, who reviewed over 200 published studies and found that the "vast and overwhelming majority" did not find a causal link, also reached this conclusion [REF',
  'John Sherry has said (2007) "Further, why do some researchers (e.g. Gentile & Anderson, 2003) continue to argue that video games are dangerous despite evidence to the contrary',
  'millions of Britons play the football pools every week',
  'David Pimentel, professor of ecology and agriculture at Cornell University, and Mario Giampietro, senior researcher at the National

In [7]:
total_p = [item for sublist in total_p for item in sublist]
total_p

['The most recent large scale meta-anlysis-- examining 130 studies with over 130,000 subjects worldwide-- concluded that exposure to violent video games causes both short term and long term aggression in players',
 'On November 29, 2010 in South Philadelphia, Pennsylvania, 16-year-old boy Kendall Anderson bludgeoned his mother to death in her sleep with a claw hammer after she took away his PlayStation [REF',
 'A meta-analysis by psychologist Jonathan Freedman, who reviewed over 200 published studies and found that the "vast and overwhelming majority" did not find a causal link, also reached this conclusion [REF',
 'John Sherry has said (2007) "Further, why do some researchers (e.g. Gentile & Anderson, 2003) continue to argue that video games are dangerous despite evidence to the contrary',
 'millions of Britons play the football pools every week',
 'David Pimentel, professor of ecology and agriculture at Cornell University, and Mario Giampietro, senior researcher at the National Resea

In [8]:
t = Tokenizer(filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',lower=True, split=' ')
t.fit_on_texts(total_p)
t.fit_on_texts(total_c)
#t.fit_on_texts(total_w)

#logging.info("vocab size: {}".format(len(t.word_index)))
encoded_premise = t.texts_to_sequences(total_p)
encoded_claim = t.texts_to_sequences(total_c)
#encoded_warrant = t.texts_to_sequences(total_w)
#sent_numbers = [len(s) for s in encoded_premise] + [len(s) for s in encoded_claim] + [len(s) for s in encoded_warrant]
#max_tokens = max(sent_numbers)
encoded_premise

[[1,
  75,
  120,
  176,
  636,
  73,
  644,
  390,
  270,
  51,
  17,
  88,
  270,
  171,
  645,
  478,
  428,
  8,
  104,
  4,
  18,
  11,
  16,
  215,
  152,
  479,
  113,
  2,
  172,
  113,
  52,
  5,
  339],
 [15,
  471,
  1090,
  100,
  5,
  561,
  1091,
  927,
  96,
  26,
  32,
  569,
  1099,
  125,
  1100,
  20,
  202,
  4,
  108,
  5,
  87,
  1101,
  17,
  6,
  751,
  752,
  58,
  146,
  572,
  472,
  20,
  441,
  7],
 [6,
  73,
  239,
  12,
  846,
  387,
  217,
  42,
  817,
  88,
  145,
  314,
  51,
  2,
  53,
  8,
  1,
  1203,
  2,
  1204,
  301,
  233,
  25,
  253,
  6,
  688,
  118,
  56,
  581,
  29,
  401,
  7],
 [286,
  530,
  33,
  112,
  85,
  511,
  794,
  76,
  72,
  187,
  109,
  143,
  800,
  125,
  186,
  653,
  4,
  285,
  8,
  11,
  16,
  21,
  770,
  497,
  177,
  4,
  1,
  801],
 [1714, 3, 1400, 305, 1, 1536, 2271, 1360, 937],
 [972,
  1610,
  391,
  3,
  1619,
  2,
  1134,
  36,
  1611,
  128,
  2,
  1620,
  1621,
  1622,
  1254,
  36,
  1,
  299,
  91,
  67

In [20]:
data[0]

{'label': 1,
 'claim': 'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world',
 'premise': 'The most recent large scale meta-anlysis-- examining 130 studies with over 130,000 subjects worldwide-- concluded that exposure to violent video games causes both short term and long term aggression in players',
 'warrant': 'The U.S. should support the Kurds only.'}

In [21]:
data[0].get("claim")

'exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world'

In [29]:
type(data)

list

In [24]:
for i in data:
    print(i.get("claim"))

exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that this exposure correlates with aggression in the real world
exposure to violent video games causes at least a temporary increase in aggression and that th

boxing is the only sport where hurting the other athlete is the goal
It is the only sport where the intention is to inflict serious injury on your opponent
boxing was very brutal
Sports related to combat skills have been a part of human culture for thousands of years
Sports related to combat skills have been a part of human culture for thousands of years
boxing may cause DP
boxing may cause DP
boxing may cause DP
Many jurisdictions, local as well as national, either ban gambling or heavily control it by licensing
legal gambling provides significant government revenue
Betting on team sports has become an important service industry in many countries
gambling, like any behavior which involves variation in brain chemistry, can become a psychologically addictive and harmful behavior
Pathological gambling is a common disorder that is associated with social costs
Pathological gambling is a common disorder that is associated with social costs
leads to adverse consequences for the gambler, othe

In [26]:
for i in data:
    premise_pool = []
    label_pool = []
    claim = i.get("claim")
    label = i.get("label")
    premise = i.get("premise")
    premise_pool += [premise]
    label_pool += [label]
    if label == 1:
        for j in data:
            c = j.get("claim")
            l = j.get("label")
            p = j.get("premise")
            if l != label and c == claim and p != premise:
                premise_pool += [p]
                label_pool += [l]

    print(json.dumps({
        "claim": claim,
        "premise": premise_pool,
        "label": label_pool,
    }))
                
                
                
                
                
    
    

AttributeError: 'list' object has no attribute 'get'

In [1]:
import random
premise_pool = [1,2,3,4,5,6,7,8,9]

In [27]:
neg_premise = random.sample(premise_pool, 1)[0]

In [28]:
neg_premise

6

In [11]:
from random import shuffle
import recsys
from recsys.evaluation.ranking import MeanReciprocalRank

TEST_DECISION = ['classical', 'invented', 'baroque', 'instrumental']
GT_DECISION = ['classical', 'instrumental', 'piano', 'baroque']
mrr = MeanReciprocalRank()
for QUERY in TEST_DECISION:
    shuffle(GT_DECISION) #Just to "generate" a different GT each time...
    mrr.load(GT_DECISION, QUERY)
mrr.compute() #in my case, returned 0.45832

ModuleNotFoundError: No module named 'recsys.evaluation'

In [12]:
import pandas as pd
import json
with open('/home/keshavsingh/keshav-nlp2019/data/complete_arc.jsonl') as f:
    data = [json.loads(line) for line in f]

In [14]:
data

[{'label': 1,
  'claim': "'Starchitects' are not ruining cities",
  'premise': 'Starchitects adhere to a more rigorous set of industry standards than do local architects.',
  'warrant': "those rigorous standards won't prevent maximum economic gain"},
 {'label': 1,
  'claim': "'Starchitects' are not ruining cities",
  'premise': "If you don't judge by personal taste, New York has amazing architecture.",
  'warrant': 'that architecture fits in with the traditional style'},
 {'label': 1,
  'claim': "'Starchitects' are not ruining cities",
  'premise': 'A small city with architectural treasures can become an international destination for architecture aficionados.',
  'warrant': 'small cities have the space or accommodations for large amounts of tourists'},
 {'label': 1,
  'claim': "'Starchitects' are not ruining cities",
  'premise': 'A small city with architectural treasures can become an international destination for architecture aficionados.',
  'warrant': 'small cities are not being ov

In [20]:
d = pd.DataFrame(data)
d

claim  label  \
0                 'Starchitects' are not ruining cities      1   
1                 'Starchitects' are not ruining cities      1   
2                 'Starchitects' are not ruining cities      1   
3                 'Starchitects' are not ruining cities      1   
4                 'Starchitects' are not ruining cities      1   
5                    3-D printing will change the world      1   
6                    3-D printing will change the world      1   
7                    3-D printing will change the world      1   
8                    3-D printing will change the world      1   
9                    3-D printing will change the world      1   
10                   3-D printing will change the world      1   
11                   3-D printing will change the world      1   
12                   3-D printing will change the world      1   
13                   3-D printing will change the world      1   
14               3-D printing will not change the world      1   
15               3-D printing will not change the world      1   
16               3-D printing will not change the world      1   
17               3-D printing will not change the world      1   
18               3-D printing will not change the world      1   
19                       Abolish Birthright Citizenship      1   
20                       Abolish Birthright Citizenship      1   
21                       Abolish Birthright Citizenship      1   
22                       Abolish Birthright Citizenship      1   
23                       Abolish Birthright Citizenship      1   
24                       Abolish Birthright Citizenship      1   
25                       Abolish Birthright Citizenship      1   
26                       Abolish Birthright Citizenship      1   
27                       Abolish Birthright Citizenship      1   
28                       Abolish Birthright Citizenship      1   
29                       Abolish Birthright Citizenship      1   
...                                                 ...    ...   
1940    Women should be encouraged to have kids at home      1   
1941                      Women should delay motherhood      1   
1942                      Women should delay motherhood      1   
1943  Women should not be encouraged to have kids at...      1   
1944  Women should not be encouraged to have kids at...      1   
1945  Women should not be encouraged to have kids at...      1   
1946  Women should not be encouraged to have kids at...      1   
1947  Women should not be encouraged to have kids at...      1   
1948  Women should not be encouraged to have kids at...      1   
1949  Women should not be encouraged to have kids at...      1   
1950  Women should not be encouraged to have kids at...      1   
1951                  Women should not delay motherhood      1   
1952                  Women should not delay motherhood      1   
1953                  Women should not delay motherhood      1   
1954                  Women should not delay motherhood      1   
1955                  Women should not delay motherhood      1   
1956                  Women should not delay motherhood      1   
1957                  Women should not delay motherhood      1   
1958                  Women should not delay motherhood      1   
1959                  Women should not delay motherhood      1   
1960                  Women should not delay motherhood      1   
1961                  Women should not delay motherhood      1   
1962                  Women should not delay motherhood      1   
1963                            Writing can be assessed      1   
1964                            Writing can be assessed      1   
1965  Young people are being irresponsible by delayi...      1   
1966  Young people are being irresponsible by delayi...      1   
1967  Young people are being irresponsible by delayi...      1   
1968  Young people are being smart by delaying the r...      1   
1969  Young people are b

In [21]:
d['warrant'].value_counts()

comments are moderated                                                                                                          2
omnivores eat a lot of meat                                                                                                     2
felons have not violated societies laws necessarily                                                                             1
it is a not a burden on countries to provide for retirees                                                                       1
Syria is out of control but what is happening there is not effecting the entire world as a whole                                1
sports makes no money for the schools and can't help fix academic issues                                                        1
defunding public schools will ultimately lead to a worse system of American education                                           1
the majority of gun violence in performed by people who have not already been background c